In [1]:
# install packages if necissary 
# ] add CSV
# ] add DataFrames
# ] add Optim

In [63]:
using CSV
using DataFrames
using WGLMakie
using Optim
using Statistics

In [64]:
alldata = CSV.read("data.csv", DataFrame);

In [65]:
size(alldata)

(20, 6)

In [66]:
data = alldata[5:end, :];

Lets make a plot of the data to see what we are working with here. 

In [67]:
f = Figure()
Axis(f[1, 1])
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x, data.y, markersize=20, color=:red)
f

Great, now lets do a linear fit to the data and see what we get

In [68]:
b_eye = 50.
m_eye = 2.

2.0

In [69]:
xx = LinRange(50, 250, 20)

20-element LinRange{Float64, Int64}:
 50.0,60.5263,71.0526,81.5789,92.1053,…,207.895,218.421,228.947,239.474,250.0

In [70]:
f = Figure()
Axis(f[1, 1])
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x, data.y, markersize=20, color=:red)

yy_eye = xx .* m_eye .+ b_eye
lines!(xx, yy_eye)

f

In [71]:
function objective(parameters)
    b = parameters[1]
    m = parameters[2]
    @show b, m
    return abs(b - 3.4) + abs(m - 17)
end

objective (generic function with 1 method)

In [72]:
function objective_2(parameters)
    b = parameters[1]
    m = parameters[2]

    y_pred = b .+ m .* data.x
    
    return sum(abs.(data.y .- y_pred))
end

objective_2 (generic function with 1 method)

In [73]:
starting_params = [b_eye + 0., m_eye]
result = optimize(objective_2, starting_params)

 * Status: success

 * Candidate solution
    Final objective value:     3.765701e+02

 * Found with
    Algorithm:     Nelder-Mead

 * Convergence measures
    √(Σ(yᵢ-ȳ)²)/n ≤ 1.0e-08

 * Work counters
    Seconds run:   0  (vs limit Inf)
    Iterations:    97
    f(x) calls:    190


In [74]:
b_abs, m_abs = Optim.minimizer(result)

2-element Vector{Float64}:
 53.74766339105346
  2.056074767629348

In [75]:
f = Figure()
Axis(f[1, 1])
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x, data.y, markersize=20, color=:red)

yy_eye = xx .* m_eye .+ b_eye
lines!(xx, yy_eye, color=:orange)

yy_abs = xx .* m_abs .+ b_abs
lines!(xx, yy_abs, color=:green)

f

# Problem 1 - Quadradic Fit

Here we will fit the data to a qadratic model instead of a linear model, we will do this by adding a quadractic term in the objective function as well as a new parameter to optimize. 

In [134]:
function objective_3(parameters)
    b = parameters[1]
    m = parameters[2]
    q = parameters[3]

    y_pred = b .+ m .* data.x .+ q .* data.x.^2
    
    return sum(abs.(data.y .- y_pred))
end

objective_3 (generic function with 1 method)

In [135]:
b_eye = 50.
m_eye = 2.
q_eye = 0.001

0.001

In [136]:
starting_params = [b_eye + 0., m_eye + 0., q_eye + 0.]
result = optimize(objective_3, starting_params)

 * Status: success

 * Candidate solution
    Final objective value:     3.339365e+02

 * Found with
    Algorithm:     Nelder-Mead

 * Convergence measures
    √(Σ(yᵢ-ȳ)²)/n ≤ 1.0e-08

 * Work counters
    Seconds run:   0  (vs limit Inf)
    Iterations:    192
    f(x) calls:    355


In [137]:
b_abs, m_abs, q_abs = Optim.minimizer(result)

3-element Vector{Float64}:
 94.76027385840413
  1.1092347687349888
  0.0041332073587093

In [138]:
f = Figure()
Axis(f[1, 1])
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x, data.y, markersize=20, color=:red)

yy_eye = xx.^2 .*q_eye .+ xx .* m_eye .+ b_eye
lines!(xx, yy_eye, color=:orange)

yy_abs = xx.^2 .*q_abs .+ xx .* m_abs .+ b_abs
lines!(xx, yy_abs, color=:green)

f

In [139]:
function objective_gauss(parameters, x, y, sigma)
    b = parameters[1]
    m = parameters[2]
    q = parameters[3]

    y_pred = b .+ m .* x + q .* x.^2
    
    return -sum(
        -log.(sigma * sqrt(2 * π)) .-0.5 .* (y .- y_pred).^2 / sigma.^2)
end

objective_gauss (generic function with 1 method)

In [140]:
starting_params = [b_eye + 0., m_eye + 0., q_eye + 0.]
result = optimize(p -> objective_gauss(p, data.x, data.y, data.sigma_y),
                  starting_params)

 * Status: success

 * Candidate solution
    Final objective value:     1.044006e+03

 * Found with
    Algorithm:     Nelder-Mead

 * Convergence measures
    √(Σ(yᵢ-ȳ)²)/n ≤ 1.0e-08

 * Work counters
    Seconds run:   0  (vs limit Inf)
    Iterations:    83
    f(x) calls:    153


In [141]:
b_gauss, m_gauss, q_gauss = Optim.minimizer(result)

3-element Vector{Float64}:
 101.51680519707841
   1.112134650293423
   0.003790790491492483

In [142]:
f = Figure()
Axis(f[1, 1])
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x, data.y, markersize=20, color=:red)

yy_eye = xx.^2 * q_eye + xx .* m_eye .+ b_eye
lines!(xx, yy_eye, color=:orange)

yy_abs = xx.^2 * q_abs + xx .* m_abs .+ b_abs
lines!(xx, yy_abs, color=:green)

yy_gauss = xx.^2 * q_gauss + xx .* m_gauss .+ b_gauss
lines!(xx, yy_gauss, color=:purple, linewidth=3)

f

Both fits look reasonable, but the gaussian fit "feels" better to me, even though they both have the same convergence measures. 

Now we do our jackknife analysis

In [143]:
ndata = size(data,1)

B_jack = zeros(ndata)
M_jack = zeros(ndata)
Q_jack = zeros(ndata)

for i in 1:ndata
    
    xcopy = copy(data.x)
    deleteat!(xcopy, i)

    ycopy = copy(data.y)
    deleteat!(ycopy, i)

    scopy = copy(data.sigma_y)
    deleteat!(scopy, i)

    starting_params = [b_eye + 0., m_eye + 0., q_eye + 0.]
    result = optimize(p -> objective_gauss(p, xcopy, ycopy, scopy),
                      starting_params)
    @assert Optim.converged(result)
    b_jack, m_jack, q_jack = Optim.minimizer(result)
    
    B_jack[i] = b_jack
    M_jack[i] = m_jack 
    Q_jack[i] = q_jack 
    
end

In [144]:
f = Figure()
Axis(f[1, 1])
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x, data.y, markersize=20, color=:red)

for i in 1:ndata
    yy_jack = xx.^2 .* Q_jack[i] + xx .* M_jack[i] .+ B_jack[i]
    lines!(xx, yy_jack, color=:green)
end

yy_gauss = xx.^2 * q_gauss + xx .* m_gauss .+ b_gauss
lines!(xx, yy_gauss, color=:purple, linewidth=3)

f

We can see that all of our best fit lines are very similar, meaning that the analysis is working, And the fits look pretty good. Lets check out the spread of parameters our analysis returned.

In [145]:
f = Figure()
Axis(f[1, 1])
scatter!(B_jack, M_jack, markersize=20, color=:red)

scatter!([b_gauss], [m_gauss], markersize=14)

f

Here it appears that we have a fairly good clustering of the returned values for M and B, and they seem to be correlated which is interesting. 

In [146]:
mean(B_jack), std(B_jack) .* sqrt((ndata - 1) / ndata)

(118.24162709855082, 69.10728984297103)

In [147]:
mean(M_jack), std(M_jack) .* sqrt((ndata - 1) / ndata)

(0.9164465263685291, 0.8194971090255541)

In [148]:
mean(Q_jack), std(Q_jack) .* sqrt((ndata - 1) / ndata)

(0.004348479802542149, 0.0023765449920179907)

In [149]:
f = Figure()
Axis(f[1, 1])
plot!(Q_jack)
# scatter!(alldata.x, alldata.y, markersize=20, color=:red)
f

So we have fairly consistant q value being generated by the jackknife analysis. The q value we get is very tiny in comparrison to the other constants and adding a quadratic term does not seem to improve very much upon the linear fit. 

# Problem 1 - MB plane

Here we investigate the m, b plane

In [150]:
function objective_gauss2(parameters, x, y, sigma)
    b = parameters[1]
    m = parameters[2]

    y_pred = b .+ m .* x 
    
    return -sum(
        -log.(sigma * sqrt(2 * π)) .-0.5 .* (y .- y_pred).^2 / sigma.^2)
end

objective_gauss2 (generic function with 1 method)

In [186]:
# Range of m,b values to plot
bvals = LinRange(0., 100., 400)
mvals = LinRange(2.0, 2.5, 400);
# Compute the objective function for each point in a grid
og = [objective_gauss2([b,m], data.x[1:1], data.y[1:1], data.sigma_y[1:1])
      for b in bvals, m in mvals]
f = Figure()
Axis(f[1, 1])
contour!(bvals, mvals, og, levels=20)
f

Here we see the diagonal locus for a single point. Lets check it out for another.

In [187]:
# Compute the objective function for each point in a grid
og = [objective_gauss2([b,m], data.x[2:2], data.y[2:2], data.sigma_y[2:2])
      for b in bvals, m in mvals]
f = Figure()
Axis(f[1, 1])
contour!(bvals, mvals, og, levels=20)
f

Here we see another diagonal locus, but at a sharper angle. Lets see them combined.

In [188]:
# Compute the objective function for each point in a grid
og1 = [objective_gauss2([b,m], data.x[1:1], data.y[1:1], data.sigma_y[1:1])
      for b in bvals, m in mvals]
og2 = [objective_gauss2([b,m], data.x[2:2], data.y[2:2], data.sigma_y[2:2])
      for b in bvals, m in mvals]
f = Figure()
Axis(f[1, 1])
contour!(bvals, mvals, og1, levels=20)
contour!(bvals, mvals, og2, levels=20)
f

In [189]:
# Compute the objective function for each point in a grid
og = [objective_gauss2([b,m], data.x[1:2], data.y[1:2], data.sigma_y[1:2])
      for b in bvals, m in mvals]
f = Figure()
Axis(f[1, 1])
contour!(bvals, mvals, og, levels=60)
f

Neat! Lets see what it looks like with all our data points. 

In [190]:
# Compute the objective function for each point in a grid
og = [objective_gauss2([b,m], data.x[1:end], data.y[1:end], data.sigma_y[1:end])
      for b in bvals, m in mvals]
f = Figure()
Axis(f[1, 1])
contour!(bvals, mvals, og, levels=80)
f

Now lets repeat the process but for our outlier rejecting version of the objective function. 

In [191]:
function objective_outliers(parameters, x, y, sigma)
    b = parameters[1]
    m = parameters[2]

    frac_bad = 0.01
    like_bad = frac_bad * (1. / 600.)

    y_pred = b .+ m .* x
    like_good = (1. - frac_bad) * 1 ./(sqrt(2*π) .* sigma) .* exp.(-0.5 * (y .- y_pred).^2 ./ sigma.^2)
    like = like_bad .+ like_good
    loglike = log.(like)

    return -sum(loglike)
end

objective_outliers (generic function with 1 method)

In [192]:
starting_params = [b_eye + 0., m_eye] # using our guessed b and m values as a starting point from which to start optimizing
result = optimize(p -> objective_outliers(p, alldata.x, alldata.y, alldata.sigma_y),
                  starting_params)
@assert Optim.converged(result)
b_out, m_out = Optim.minimizer(result)

2-element Vector{Float64}:
 32.71335736732801
  2.252659398988028

In [193]:
# Compute the objective function for each point in a grid
og = [objective_outliers([b,m], data.x[1:end], data.y[1:end], data.sigma_y[1:end])
      for b in bvals, m in mvals]
f = Figure()
Axis(f[1, 1])
contour!(bvals, mvals, og, levels=250)
f

Lets expand the search space and look for punks

In [184]:
# Range of m,b values to plot
bvals = LinRange(0., 900., 600)
mvals = LinRange(-1., 4, 600);
# Compute the objective function for each point in a grid
og = [objective_outliers([b,m], alldata.x[1:end], alldata.y[1:end], alldata.sigma_y[1:end])
      for b in bvals, m in mvals]
f = Figure()
Axis(f[1, 1])
contour!(bvals, mvals, og, levels=150) # contour plot
f

FOUND EM! GET OUTTA HERE! SCRAM! Looks like there are some fake minima hiding around. I can see them in the density of the countours.

# Problem 3 - reparametrization

Lets try to make m and b less correlated by changing our parametrization. We will try to do this by including information about the mean value. Not sure what it will do but lets see. 

In [198]:
mean = mean(data.x)

function objective_outliers_new(parameters, x, y, sigma)
    b = parameters[1]
    m = parameters[2]

    frac_bad = 0.01
    like_bad = frac_bad * (1. / 600.)

    y_pred = b .+ m .* (x .- mean) .+ mean
    like_good = (1. - frac_bad) * 1 ./(sqrt(2*π) .* sigma) .* exp.(-0.5 * (y .- y_pred).^2 ./ sigma.^2)
    like = like_bad .+ like_good
    loglike = log.(like)

    return -sum(loglike)
end

LoadError: cannot assign a value to variable Statistics.mean from module Main

In [196]:
# Compute the objective function for each point in a grid
og = [objective_outliers_new([b,m], data.x[1:end], data.y[1:end], data.sigma_y[1:end])
      for b in bvals, m in mvals]
f = Figure()
Axis(f[1, 1])
contour!(bvals, mvals, og, levels=250)
f

LoadError: UndefVarError: mean not defined

In [108]:
f = Figure()
Axis(f[1, 1])
errorbars!(alldata.x, alldata.y, alldata.sigma_y)
scatter!(alldata.x, alldata.y, markersize=20, color=:red)
f

In [112]:
starting_params = [b_eye + 0., m_eye + 0., q_eye + 0.]
result = optimize(p -> objective_gauss(p, alldata.x, alldata.y, alldata.sigma_y),
                  starting_params)
@assert Optim.converged(result)
b_bad, m_bad, q_bad = Optim.minimizer(result)

3-element Vector{Float64}:
 322.61356256951655
   0.4509894771158308
   0.0005682575219269736

In [113]:
f = Figure()
Axis(f[1, 1])
errorbars!(alldata.x, alldata.y, alldata.sigma_y)
scatter!(alldata.x, alldata.y, markersize=20, color=:red)

yy_bad = xx.^2 * q_bad + xx .* m_bad .+ b_bad
lines!(xx, yy_bad, color=:purple, linewidth=3)

f

In [37]:
function objective_outliers(parameters, x, y, sigma)
    b = parameters[1]

    frac_bad = 0.01
    like_bad = frac_bad * (1. / 600.)

    y_pred = b .+ m .* x
    like_good = (1. - frac_bad) * 1 ./(sqrt(2*π) .* sigma) .* exp.(-0.5 * (y .- y_pred).^2 ./ sigma.^2)
    like = like_bad .+ like_good
    loglike = log.(like)

    return -sum(loglike)
end

objective_outliers (generic function with 1 method)

In [38]:
starting_params = [b_eye + 0., m_eye]
result = optimize(p -> objective_outliers(p, alldata.x, alldata.y, alldata.sigma_y),
                  starting_params)
@assert Optim.converged(result)
b_out, m_out = Optim.minimizer(result)

LoadError: UndefVarError: m not defined

In [39]:
starting_params = [700 + 0., -0.5]
result = optimize(p -> objective_outliers(p, alldata.x, alldata.y, alldata.sigma_y),
                  starting_params)
@assert Optim.converged(result)
b_punk, m_punk = Optim.minimizer(result)

LoadError: UndefVarError: m not defined

In [40]:
f = Figure()
Axis(f[1, 1])
errorbars!(alldata.x, alldata.y, alldata.sigma_y)
scatter!(alldata.x, alldata.y, markersize=20, color=:red)

yy_bad = xx .* m_bad .+ b_bad
lines!(xx, yy_bad, color=:purple, linewidth=3)

yy_out = xx .* m_out .+ b_out
lines!(xx, yy_out, color=:green, linewidth=3)

yy_punk = xx .* m_punk .+ b_punk
lines!(xx, yy_punk, color=:blue, linewidth=3)

f

LoadError: UndefVarError: m_out not defined